# Language clustering in the Million Song Dataset lyrics

musiXmatch contributed the lyrics of 237,662 tracks to the Million Song Dataset. These lyrics are limited to a dictionary of the top 5,000 words across the set, which contains several languages. The dataset doesn't tell in which language each song is written, nor to which language(s) each word might belong. We do not know how many languages there are in the dataset, nor their proportions in the dictionary. Nevertheless, it may be useful to group words and/or songs per language. 

This notebook uses hierarchical clustering to group words by language, based on word co-occurences in the dataset. The rationale for using hiearchical clustering over other clustering methods is that a) we do no know how many clusters/languages there might be in the dataset and b) we can expect clusters/languages to have very different word counts. Hierarchical clustering places every word on a same footing and allows for the detection of clusters of vastly varying sizes.

The analysis is based on the musiXmatch dataset, the official lyrics collection for the Million Song Dataset, available at: http://labrosa.ee.columbia.edu/millionsong/musixmatch


## Computation

The analysis was written in Clojure and was run offline. Its code can be found [here on github](https://github.com/belovehq/msd-languages).

* The musiXmatch dataset was first loaded into an H2 SQL database. A matrix of word co-occurences was then assembled, with element (i,j) the number of tracks in which words (i) and (j) appear together (standardised by the total number of tracks ind which word (i) appears). Each word is hence represented in the matrix by the vector of its "co-words" in the dataset. The rationale behind this is that if two words have the same set of co-words, then these two words are likely to belong to the same language.

* A hierarchical linkage of the words was performed in Matlab using cosine distance and unweighted average to compute the distance between clusters. The resulting dendrogram was sliced at different levels to produce clusterings with between two and thirty clusters. 

* To help decide how many clusters to consider, each cluster was submitted to the [language-detection](https://code.google.com/archive/p/language-detection/) Java library. For each cluster, the detection was performed over a thousand random phrases of fifty words. Each cluster was allocated the language that seemed the most likely.

* Each cluster was also attributed a measurement of "compactness", calculated as the cosine of the angle between the cluster and the set of words engendered by the cluster. The higher this cosine, the least the cluster correlates with other words in the dataset. 

* Finally, the database was queried again in order to produce a sample list of artists for every cluster (naively: top x artists that use the top y words in the cluster)

The output of the computation was stored in an edn file, which is the starting point of this notebook. This edn file contains a copy of the parameters of the analysis, which follow.

In [4]:
(def data (read-string (slurp "../data/out.edn" :encoding "UTF-8")))
(->> data
     :params
     (reduce-kv #(assoc %1 %2 (str %3)) {}))

The table below shows an example of clustering with 5 clusters. Cluster sizes vary significantly, with the English cluster a hundred times larger than the Finnish cluster. Language probabilities show that the Spanish and Swedish clusters may need splitting into language subgroups.

In [5]:
(defn show-clusters [n]
    (let [clusters (get-in data [:clusterings (- n 2) :clusters])]
        (map #(array-map 
                 "Language" (get-in data [:languages (get-in % [:language :id])])
                 "Probability" (get-in % [:language :proba])
                 "Words" (:count %)
                 "Top words" (apply str (interpose ", " (take 10 (:words %))))
                 "Compactness" (double (:compactness %))
                 "Sample artists"  (apply str (interpose ", " (take 5 (:artists %)))))
              clusters)))

(show-clusters 5)

## Locating the optimal number of clusters

### Average Probabilities

The chart below displays the average language probability across clusters when the number of clusters varying between four and thirty. The optimal number of clusters would seem to be located circa 13-15 clusters. 

In [6]:
(import [com.twosigma.beakerx.chart.xychart Plot]
        [com.twosigma.beakerx.chart.xychart.plotitem Line])

(def lang-stats (map :language-stats (:clusterings data)))

(doto (Plot.) (.setTitle "Language Probabilities")
              (.setXLabel "Number of Clusters") 
              (.setYLabel "Probability") 
              (.setXBound 4 30)
              (.setYBound 0.85 1.005) 
              (.add (doto (Line.) (.setDisplayName "Weighted Average")
                                  (.setX (map :clusters lang-stats))
                                  (.setY (map :wavg lang-stats))))
              (.add (doto (Line.) (.setDisplayName "Arithmetic Mean (count > 1)")
                                  (.setX (map :clusters lang-stats))
                                  (.setY (map :avg lang-stats))))
              (.setInitWidth 800) 
              (.setOmitCheckboxes true))

### Cluster Fragmentation

The chart below shows that increasing the number of clusters above 13 mostly contributes to cluster fragmentation. Indicators of fragmentation here are a) one-word clusters and b) duplicate detected languages across clusters (excluding one-word clusters to avoid double-counting). This chart, together with the above one, suggests that 13 clusters might be the place where to start looking. 

In [7]:
(doto (Plot.) (.setTitle "Cluster Fragmentation")
              (.setXLabel "Number of Clusters") 
              (.setYLabel "Irregularities") 
              (.setXBound 4 30)
              (.setYBound 0 15) 
              (.add (doto (Line.) (.setDisplayName "One-Word Clusters")
                                  (.setX (map :clusters lang-stats))
                                  (.setY (map :=1 lang-stats))))
              (.add (doto (Line.) (.setDisplayName "Duplicate Languages")
                                  (.setX (map :clusters lang-stats))
                                  (.setY (map :dupe lang-stats))))
              (.add (doto (Line.) (.setDisplayName "All")
                                  (.setX (map :clusters lang-stats))
                                  (.setY (map #(+ (:dupe %) (:=1 %)) lang-stats))))
             
              (.setInitWidth 800) 
              (.setOmitCheckboxes true))

### Optimal Clustering

The table below show the 13 clusters that seem optimal in the above charts, followed by the content of the 'Swedish' cluster. We note the high language probabilities across clusters, as well as the good match between detected language, sample words and sample artists. A commentary of this table follows below.

In [8]:
(show-clusters 13)

In [9]:
;Swedish cluster

(get-in data [:clusterings (- 13 2) :clusters 6 :words])

[jag, det, och, som, vi, är, på, har, om, att, mig, med, så, kan, nu, jeg, av, var, för, min, inte, ett, din, ska, allt, när, meg, dom, kom, eg, ingen, dag, å, mitt, går, här, aldrig, vad, ut, kommer, bara, blir, oss, finns, igen, där, liv, ikke, ditt, vil, bli, får, fr, gå, mina, hur, då, ner, leva, når, upp, ge, livet, från, alltid, sig, vara, ingenting, kvar, står]

The skew in size between clusters is remarkable; from 3420 words in the English cluster, to only one in the Turkish cluster. This is consistent with our knowledge that the musicXmatch dictionary contains the top 5000 words in the dataset across all languages mixed; the most prominent words in 'smaller' languages are under-represented compared to less prominent words in English.

There are no specific clusters for Norwegian and Danish, whose vocabularies are similar to Swedish. The cluster tagged as 'Swedish' should therefore be seen as an umbrella for all three languages. Similarly, Croatian should be seen as Serbo-Croatian. 

The 'larger' languages canibalise the 'smaller' ones. For example, 'in' and 'me' are counted as English whereby they also respectively belong to German and French (among other languages). The association of these words to English was stronger in the co-occurence matrix because of the greater count of English songs in the dataset. As a result, a cluster is not an complete dictionary; the complete dictionary for a 'smaller' cluster should reintegrate some words from 'larger' clusters. The further down the line a cluster is, the more words will need to be reintegrated from larger clusters. At the limit, some languages are completely subsumed to larger clusters. For example, Romanian is absent from the list despite the presence of Romanian artists in the dataset. 

Cannibalisation directly impacts the Compactness measure. Because they are cannibalised by larger ones, smaller clusters will be less compact. Compactness is also influenced by artists borrowing words from various languages in their work; this is most likely to reduce the compactness of smaller languages by virtue of relative language representations in the dataset. Because it is so correlated to language representation in the dataset, the Compactness measure is therefore of limited utility, except maybe to compare like-for-like e.g.:
* The Swedish cluster has less words than the Portuguese one but a higher compactness measure. This would seem to indicate that the Swedish cluster is indeed much more compact that the Portuguese one, possibly because the latter is cannibalised by several 'larger' latin languages.
* The Turkish cluster, which only has one word, has a higher measure of compactness than some larger clusters. This seems to indicate that the word 'bir' might be a valid indicator of the Turkish language. The artists who use of the words indeed do so part of songs written in Turkish, or part of Turkish phrases (e.g. the band *Deine Lieblings Rapper* sing in German but nonetheless use 'bir' in the Turkish phrase 'Bir iki üç' in their song *Mit Stil*). We also note that 'bir' is singled out as a separate cluster by the clustering algorithm with as low as 7 clusters in total (see below), a point at which the algorithm still doesn't distinguish French, Italian and Portuguese from Spanish.

In [10]:
(show-clusters 7)

All this considered, the above 13 clusters seem a good point of departure to locate languages in the dataset, even though we know that some consideration will need to be given to common words between languages and to artists borrowing words from various languages. Let us now examine the effect of decreasing or increasing the number of clusters.


## Varying the number of clusters

### Decreasing the number of clusters

Direct observation confirms that clusters degrade below 13 clusters. For example, Italian merges with Spanish as soon as we move down to 12 clusters. 

In [11]:
(show-clusters 12)

### Increasing the number of clusters

The dispersion chart indicated that cluster dispersion increases beyond 13 clusters, with a slope of one except for some plateaus that may deserve attention: 

* Plateaus at 19, 21 and 23 clusters are due to spurious language detection artefacts: the tiny clusters that are spun off at these stages are analysed as new Slovene, Norwegian and Romanian clusters, but this isn't supported by the language of the artists that use them. 

* In contrast, the plateau at 18 clusters corresponds to the appearance of a new cluster 'wa ga ka kimi', which was spun-off from the English cluster. Our language detection library identifies this cluster as Swahili. However, querying the database shows that artists that use these words together are mostly Japanese. It may therefore make sense to associates this cluster as a marker of Japanese in the dataset.

In [12]:
(show-clusters 18)

## Final cluster allocation

Based on the above observations, we are keeping the earlier list of 13 clusters, to which we are adding the Japanese cluster. Further work on the Million Song Dataset will test the utility/robustness of this list.  

In [13]:
(def final 
    (let [dictionary (:words data)      
      thirteen-clusters (get-in data [:clusterings (- 13 2) :clusters])
      japanese-cluster  (set (get-in data [:clusterings (- 18 2) :clusters 9 :wordids]))
      language-order    (-> (map (fn [{{l :id} :language}] (name l)) thirteen-clusters)
                            (zipmap (range))
                            (assoc "ja" 8.5))
      word-to-row       (fn [language wordid] (let [{:keys [stem word]} (get dictionary wordid)] 
                                                (array-map "language" (if (japanese-cluster wordid) "ja" (name language)) 
                                                           "wordid" wordid 
                                                           "stem" stem
                                                           "word" word)))
      cluster-to-rows (fn [{{language :id} :language wordids :wordids}] 
                            (map (partial word-to-row language) wordids))
      row-order (fn [{language "language" wordid "wordid"}] (vector (get language-order language) wordid))]

  (->> thirteen-clusters
       (map cluster-to-rows)
       (apply concat)
       (sort-by row-order))))

final

And we save the list to MSD format.

In [14]:
(let [f "../data/mxm_clustered_dictionary.txt"
      s (->> final
             (sort-by #(get % "wordid"))
             (map #(str (get % "stem") "<SEP>" (get % "language") \newline))
             (apply str))]
  (spit f s :encoding "UTF-8")
  f)

../data/mxm_clustered_dictionary.txt